# Investigate 

## Setup notebook
Import our required packages and set default plotting options.

In [ ]:
# Enable autoreloading of our modules. 
# Most of the code will be located in the /src/ folder, 
# and then called from the notebook.
%matplotlib inline
%reload_ext autoreload
%autoreload

In [ ]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os
import decimal
import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
from plotly import tools
import plotly.io as pio
from scipy import stats
import math
import matplotlib
from matplotlib import cm
import colorlover as cl
from tqdm import tqdm_notebook
from ipywidgets import widgets, Output
from IPython.display import display, clear_output, Image, HTML
from scipy import stats
from sklearn.metrics import confusion_matrix
import matplotlib.pyplot as plt
from matplotlib.ticker import MultipleLocator
from matplotlib.lines import Line2D
from cycler import cycler
from scipy.interpolate import interp1d
from pandas.api.types import CategoricalDtype
import seaborn as sns
sns.set(style="white")
from scipy import interpolate
from tqdm import tqdm

In [ ]:
# Matplot lib default settings
plt.rcParams["figure.figsize"] = (10,6)
plt.rcParams['axes.grid']=True
plt.rcParams['grid.alpha'] = 0.5
plt.rcParams['grid.color'] = "grey"
plt.rcParams['grid.linestyle'] = "--"
plt.rcParams['axes.grid']=True

# https://stackoverflow.com/a/20709149
# matplotlib.rcParams['text.usetex'] = True

matplotlib.rcParams['text.latex.preamble'] = [
       r'\usepackage{siunitx}',   # i need upright \micro symbols, but you need...
       r'\sisetup{detect-all}',   # ...this to force siunitx to actually use your fonts
       r'\usepackage{helvet}',    # set the normal font here
       r'\usepackage{amsmath}',
       r'\usepackage{sansmath}',  # load up the sansmath so that math -> helvet
       r'\sansmath',              # <- tricky! -- gotta actually tell tex to use!
]  

## Import data
Import our data from the `./data/interim/` folder and load it into pandas dataframes. 

In [ ]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_waves = df_from_csv('waves.csv', index_col=[0, 1])
df_tides = df_from_csv('tides.csv', index_col=[0, 1])
df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_sites = df_from_csv('sites.csv', index_col=[0])
df_sites_waves = df_from_csv('sites_waves.csv', index_col=[0])
df_profile_features_crest_toes = df_from_csv('profile_features_crest_toes.csv', index_col=[0,1])

# Note that the forecasted data sets should be in the same order for impacts and twls
impacts = {
    'forecasted': {
    'postintertidal_slope_sto06': df_from_csv('impacts_forecasted_postintertidal_slope_sto06.csv', index_col=[0]),
    'postmean_slope_sto06': df_from_csv('impacts_forecasted_postmean_slope_sto06.csv', index_col=[0]),
    'preintertidal_slope_sto06': df_from_csv('impacts_forecasted_preintertidal_slope_sto06.csv', index_col=[0]),
    'premean_slope_sto06': df_from_csv('impacts_forecasted_premean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }

twls = {
    'forecasted': {
    'postintertidal_slope_sto06': df_from_csv('twl_postintertidal_slope_sto06.csv', index_col=[0,1]),
    'postmean_slope_sto06': df_from_csv('twl_postmean_slope_sto06.csv', index_col=[0,1]),
    'preintertidal_slope_sto06': df_from_csv('twl_preintertidal_slope_sto06.csv', index_col=[0,1]),
    'premean_slope_sto06': df_from_csv('twl_premean_slope_sto06.csv', index_col=[0,1]),
    }
}
print('Done!')

# Gather data into one dataframe
For plotting, gather all our data into one dataframe.

In [ ]:
# Which forecasted impacts dataframe should we use to assess prediction performance?
df_selected_forecast = impacts['forecasted']['postintertidal_slope_sto06']

# Create df with all our data
df = impacts['observed'].merge(
    df_sites_waves, left_index=True, right_index=True)

# Join observed/forecasted regimes
df_forecasted = df_selected_forecast.rename(
    {'storm_regime': 'forecasted_regime'
    }, axis='columns').forecasted_regime
df = pd.concat([df, df_forecasted], axis=1)

# Create new accuracy column which categorises each prediction
df.loc[(df.storm_regime == 'swash') & (df.forecasted_regime == 'swash'), 'accuracy'] = 'correct swash'
df.loc[(df.storm_regime == 'collision') & (df.forecasted_regime == 'collision'), 'accuracy'] = 'correct collision'
df.loc[(df.storm_regime == 'swash') & (df.forecasted_regime == 'collision'), 'accuracy'] = 'overpredicted swash'
df.loc[(df.storm_regime == 'collision') & (df.forecasted_regime == 'swash'), 'accuracy'] = 'underpredicted collision'

print('df columns:\n===')
for col in sorted(df.columns):
    print(col)

# Create plots

## Variable pairplot, by observed storm impact
Create pairplot of selected variables and look for relationships between each. Colors represent the different observed storm impact regimes.

In [ ]:
g = sns.pairplot(
    data=df,
    hue='storm_regime',
    dropna=True,
    palette={
        'swash': 'blue',
        'collision': 'orange',
        'overwash': 'red'
    },
    plot_kws=dict(s=20, edgecolor="white", linewidth=0.1, alpha=0.1),
    vars=['beta_prestorm_mean',
          'beta_poststorm_mean',
          'beta_diff_mean',
          'swash_pct_change',
          'width_msl_change_m',
          'width_msl_change_pct',
          'Exscum'])
g.savefig('11_pairplot_observed_impacts.png')

## Variable pairplot, by observed/prediction class
Create pairplot of selected variables and look for relationships between each. Colors represent the different observed/prediction classes.

In [ ]:
g = sns.pairplot(
    data=df,
    hue='accuracy',
    dropna=True,
    palette={
        'correct swash': 'blue',
        'correct collision': 'green',
        'overpredicted swash': 'orange',
        'underpredicted collision': 'red',
    },
    plot_kws=dict(s=20, edgecolor="white", linewidth=0.1, alpha=0.1),
    vars=['beta_prestorm_mean',
          'beta_poststorm_mean',
          'beta_diff_mean',
          'swash_pct_change',
          'width_msl_change_m',
          'width_msl_change_pct',
          'Exscum'])
g.savefig('11_pairplot_accuracy_classes.png')


## Pre/post storm slope by observed/predicted class

In [ ]:
# First create a melted dataframe since our coulmn's aren't exactly as they should be for plotting
df_temp = df.copy()
df_temp = df_temp.reset_index()

df_melt = pd.melt(
    df_temp,
    id_vars=['site_id', 'accuracy'],
    value_vars=['beta_prestorm_mean', 'beta_poststorm_mean'],
    var_name='profile_type',
    value_name='beta_mean')

df_melt.loc[df_melt.profile_type == 'beta_prestorm_mean','profile_type'] = 'prestorm'
df_melt.loc[df_melt.profile_type == 'beta_poststorm_mean','profile_type'] = 'poststorm'
df_melt.head()

In [ ]:
f, ax = plt.subplots(figsize=(6,5))

cats = ['correct swash', 'overpredicted swash','underpredicted collision','correct collision']

# Plot the orbital period with horizontal boxes
sns.boxplot(
    data=df_melt,
    x="accuracy",
    y="beta_mean",
    hue="profile_type",
    order=cats
)

group_labels = [x.replace(' ','\n') for x in cats]
ax.set_xticklabels(group_labels)

# Setup ticks and grid
ax.xaxis.grid(True)
major_ticks = np.arange(-1, 1, 0.05)
minor_ticks = np.arange(-1, 1, 0.01)
ax.set_yticks(major_ticks)
ax.set_yticks(minor_ticks, minor=True)
ax.grid(which='both')
ax.grid(which='minor', alpha=0.3,linestyle='--')
ax.grid(which='major', alpha=0.8,linestyle='-')

ax.set_ylim([-0.02,0.3])

f.savefig('11_prepost_slopes_accuracy_classes.png',dpi=600)

## Change in slope by observed/predicted class

In [ ]:
f, ax = plt.subplots(figsize=(6,5))

cats = ['correct swash', 'overpredicted swash','underpredicted collision','correct collision']

# Plot the orbital period with horizontal boxes
sns.boxplot(
    data=df,
    x="accuracy",
    y="beta_diff_mean",
    order=cats
)

group_labels = [x.replace(' ','\n') for x in cats]
ax.set_xticklabels(group_labels)

# Setup ticks and grid
ax.xaxis.grid(True)
major_ticks = np.arange(-1, 1, 0.05)
minor_ticks = np.arange(-1, 1, 0.01)
ax.set_yticks(major_ticks)
ax.set_yticks(minor_ticks, minor=True)
ax.grid(which='both')
ax.grid(which='minor', alpha=0.3,linestyle='--')
ax.grid(which='major', alpha=0.8,linestyle='-')

ax.set_ylim([-0.2,0.2])

f.savefig('11_change_in_slopes_accuracy_classes.png',dpi=600)

## Swash zone volume change histogram

How much does the beach width change variation can we expect in the swash regime?

In [ ]:
f, ax = plt.subplots(figsize=(5,4))

sns.distplot(df.loc[df.storm_regime=='swash'].width_msl_change_pct.dropna(), 
             kde=False);

ax.set_title('Distribution of beach width change for swash regime')
ax.set_xlabel('$\Delta$ beach width (%)')
ax.set_ylabel('Count')

f.savefig('11_change_in_beach_width.png',dpi=600)

# Find correlations between variables

## Create correlogram

In [ ]:
from matplotlib.patches import Ellipse
def corrplot(data, pvalues, labels):
    """Creates a correlation plot of the passed data.
    The function returns the plot which can then be shown with
    plot.show(), saved to a file with plot.savefig(), or manipulated
    in any other standard matplotlib way.
    data is the correlation matrix, a 2-D numpy array containing
    the pairwise correlations between variables;
    pvalues is a matrix containing the pvalue for each corresponding
    correlation value; if none it is assumed to be the zero matrix
    labels is an array containing the variable names
    https://github.com/louridas/corrplot/blob/master/corrplot.py
    """

    plt.figure(1)

    column_labels = labels
    row_labels = labels
    
    f = plt.figure(figsize=(8,8))
    ax = plt.subplot(1, 1, 1, aspect='equal')

    width, height = data.shape
    num_cols, num_rows = width, height

    if pvalues is None:
        pvalues = np.zeros([num_rows, num_cols])
        
    shrink = 0.9

    poscm = cm.get_cmap('Blues')
    negcm = cm.get_cmap('Oranges')

    for x in range(width):
        for y in range(height):
            d = data[x, y]
            c = pvalues[x, y]
            rotate = -45 if d > 0 else +45
            clrmap = poscm if d >= 0 else negcm
            d_abs = np.abs(d)
            ellipse = Ellipse((x, y),
                              width=1 * shrink,
                              height=(shrink - d_abs*shrink),
                              angle=rotate)
            ellipse.set_edgecolor('black')
            ellipse.set_facecolor(clrmap(d_abs))
            if c > 0.05:
                ellipse.set_linestyle('dotted')
                ellipse.set_alpha(0.5)
            ax.add_artist(ellipse)

    ax.set_xlim(-1, num_cols)
    ax.set_ylim(-1, num_rows)
        
    ax.xaxis.tick_top()
    xtickslocs = np.arange(len(row_labels))
    ax.set_xticks(xtickslocs)
    ax.set_xticklabels(row_labels, rotation=30, fontsize='small', ha='left')

    ax.invert_yaxis()
    ytickslocs = np.arange(len(row_labels))
    ax.set_yticks(ytickslocs)
    ax.set_yticklabels(column_labels, fontsize='small')

    return plt

In [ ]:
# Calculate correlation coefficient and p-values
# https://stackoverflow.com/a/24469099
corr = df.corr(method ='pearson') 
n=len(corr.columns)
t=corr*np.sqrt((n-2)/(1-corr*corr))
pvals = stats.t.cdf(t, n-2)

plot = corrplot(corr.values, pvals, corr.columns.tolist())
plot.show()

## Create regression plot between two variables

In [ ]:
from scipy import stats

# x_col = 'beta_prestorm_intertidal'
# y_col = "beta_diff_intertidal"
# data = df.loc[df.storm_regime=='swash']

# y_col = 'total_vol_change'
# x_col = "Pxscum"
# data = df

y_col = 'prestorm_cum_exposed_vol'
x_col = "Exscum"
c_col = 'total_vol_change'
data = df

slope, intercept, r_value, p_value, std_err = stats.linregress(
    data.dropna()[x_col].values,
    data.dropna()[y_col].values)

fig = plt.figure(
    figsize=(6, 4), dpi=150, facecolor='w', edgecolor='k')
ax = fig.add_subplot(111)

scatter = ax.scatter(
    x=data.dropna()[x_col].values,
    y=data.dropna()[y_col].values,
    c=data.dropna()[c_col].values,
    s=1, 
    vmin=-150, vmax=0,
)

ax.set_xlabel(x_col)
ax.set_ylabel(y_col)
ax.set_ylim(0,20000)

cbar = plt.colorbar(scatter)
cbar.set_label(c_col)

ax.grid(True, linestyle="--", alpha=0.2, color='grey', linewidth=1)

plt.show()

# Calculate berm shape index

In [ ]:
df_profiles
df_profile_features_crest_toes

berm_shape = []
grouped = df_profiles.dropna(subset=['z']).xs('prestorm',level='profile_type').groupby('site_id')
for site_id, df_site in tqdm(grouped):
    features = df_profile_features_crest_toes.loc[(site_id,'prestorm')]
    
    # Get x-coordinate at z=0
    x_last = df_site.iloc[-1].name[1]
    z_last = 0
    
    # Get coordinates of dune toe
    x_first = features.dune_toe_x
    z_first = features.dune_toe_z
    
    # If there is no dune toe, get dune crest
    if np.isnan(x_first):
        x_first = features.dune_crest_x
        z_first = features.dune_crest_z
    
    # If no dune crest, use nan
    if np.isnan(x_first):
        berm_shape.append({'site_id': site_id,
                     'prestorm_berm_curvature': np.nan})
        continue

    # Fit straight line between start and end points
    segment = (df_site.loc[(df_site.index.get_level_values('x')>=x_first)&
                (df_site.index.get_level_values('x')<=x_last)])
    x_segment = segment.index.get_level_values('x')
    z_segment = segment.z
    f = interpolate.interp1d([x_first,x_last],[z_first,z_last])
    z_straight = f(x_segment)

    area = np.trapz(y=z_straight-z_segment, x=x_segment)
    length = x_last-x_first
    
    normalized_curvature = area
#     normalized_curvature = area / length
    berm_shape.append({'site_id': site_id,
                 'prestorm_berm_curvature': normalized_curvature})

# Convert to dataframe    
df_berm_shape = pd.DataFrame(berm_shape)
df_berm_shape = df_berm_shape.set_index('site_id')

# Join onto our big dataframe
df = df.drop(columns=['prestorm_berm_curvature'], errors='ignore')
df = pd.concat([df, df_berm_shape], axis=1)

df_berm_shape.head()


# Check wave timeseries
How much does wave height vary alongshore between sites?

In [ ]:
from dateutil.parser import parse
sites = ['NARRA0001', 'NARRA0012', 'NARRA0024']

fig = plt.figure(
    figsize=(6, 4), dpi=150, facecolor='w', edgecolor='k')
ax = fig.add_subplot(111)

for site_id in sites:
    print(site_id)
    x = [parse(t) for t in df_waves.xs(site_id,level='site_id').index]
    y = df_waves.xs(site_id,level='site_id').Hs
    ax.plot(x,y)
    
plt.show()

# Cumulative sum of available prestorm volume?

In [ ]:
# At each site, determine relationship between height and available volume
data = []
site_ids = df_sites.index.values
for site_id in site_ids:
    df_profile = df_profiles.xs([site_id, 'prestorm'],
                                level=['site_id',
                                       'profile_type']).dropna(subset=['z'])
    x_profile = df_profile.index.get_level_values('x').values
    z_profile = df_profile.z.values
    
    z_vals = np.arange(min(df_profile.z),max(df_profile.z),0.01)
    
    for z in z_vals:
        i_start = np.where((z_profile > z))[0][-1]
        x_start = x_profile[i_start]
        x_end = x_profile[-1]
        mask = (x_start <= x_profile) & (x_profile <= x_end)
        vol = np.trapz(z_profile[mask], x=x_profile[mask])
        data.append({'site_id': site_id,'z':z,'prestorm_vol':vol})
        
df_prestorm_vols_by_z = pd.DataFrame(data)
df_prestorm_vols_by_z = df_prestorm_vols_by_z.set_index(['site_id','z'])
df_prestorm_vols_by_z.head()

In [ ]:
df_twl = twls['forecasted']['preintertidal_slope_sto06']
df_twl['z'] = df_twl.R_high.round(2)

df_twl = df_twl.join(df_prestorm_vols_by_z, on=['site_id','z'])
df_twl = df_twl.drop(columns=['z'])

df_site_cum_exposed_vols = df_twl.groupby('site_id').prestorm_vol.sum().to_frame()
df_site_cum_exposed_vols = df_site_cum_exposed_vols.rename({'prestorm_vol':'prestorm_cum_exposed_vol'},axis=1)

# # Join onto main dataframe
df = df.drop(columns=['prestorm_cum_exposed_vol'], errors='ignore')
df = pd.concat([df, df_site_cum_exposed_vols], axis=1)

df_site_cum_exposed_vols.head()


# PCA?

In [ ]:
X[0]

In [ ]:
from sklearn import decomposition
from sklearn.preprocessing import StandardScaler

target_col = 'swash_pct_change'
training_cols = ['beta_prestorm_mean','beta_prestorm_intertidal','prestorm_dune_vol','prestorm_swash_vol','width_msl_prestorm','Pxscum','prestorm_berm_curvature','prestorm_cum_exposed_vol']

df_pca = df[training_cols+[target_col]].dropna()
df_pca_data_only =  df_pca.drop(target_col,axis=1)

# input data
X = df_pca_data_only.values
X = StandardScaler().fit_transform(X)

# target
y = df_pca[target_col]

# pca
pca = decomposition.PCA(n_components=2)
pca.fit(X)

X = pca.transform(X)


fig = plt.figure(
    figsize=(6, 4), dpi=150, facecolor='w', edgecolor='k')
ax = fig.add_subplot(111)

scatter = ax.scatter(
    x=X[:,0],
    y=X[:,1],
    c=y,
    s=0.5, 
    vmin=-1, vmax=0,
)

# ax.set_xlabel(x_col)
# ax.set_ylabel(y_col)
# ax.set_ylim(0,20000)

cbar = plt.colorbar(scatter)
# cbar.set_label(c_col)

# ax.grid(True, linestyle="--", alpha=0.2, color='grey', linewidth=1)

plt.show()


In [ ]:
df_pca_dims = pd.DataFrame(pca.components_, columns=list(df_pca_data_only.columns))

df_pca_dims.iloc[0]
# pca.explained_variance_ratio_